In [1]:
### polyphase channelizer
import numpy as np
from scipy.signal import firwin, lfilter, freqz
from scipy.signal import butter, filtfilt, resample
from scipy.fft import fft, ifft, fftshift

import plotly.graph_objects as go
import plotly.express as px

In [2]:
x_f_1 = np.random.randn(1000) + 0j
x_f_1[100:900] *= 1e-6
x_f_1_original = x_f_1.copy()
x_t_1 = ifft(x_f_1)*len(x_f_1)
x_t_1 = resample(x_t_1, 4000)

x_f_2 = np.random.randn(1000) + 0j
x_f_2[200:800] *= 1e-6
x_t_2 = ifft(x_f_2)*len(x_f_2)
x_f_2_original = x_f_2.copy()
x_t_2 = resample(x_t_2, 4000)
x_t_2 *= np.exp(1j*2*np.pi*1000*np.arange(len(x_t_2))/4000)

x_f_3 = np.random.randn(1000) + 0j
x_f_3[300:700] *= 1e-6
x_t_3 = ifft(x_f_3)*len(x_f_3)
x_f_3_original = x_f_3.copy()
x_t_3 = resample(x_t_3, 4000)
x_t_3 *= np.exp(1j*2*np.pi*2000*np.arange(len(x_t_3))/4000)

x_f_4 = np.random.randn(1000) + 0j
x_f_4[400:600] *= 1e-6
x_t_4 = ifft(x_f_4)*len(x_f_4)
x_f_4_original = x_f_4.copy()
x_t_4 = resample(x_t_4, 4000)
x_t_4 *= np.exp(1j*2*np.pi*3000*np.arange(len(x_t_4))/4000)

x_f_1 = fft(x_t_1)/len(x_t_1)
x_f_2 = fft(x_t_2)/len(x_t_1)
x_f_3 = fft(x_t_3)/len(x_t_1)
x_f_4 = fft(x_t_4)/len(x_t_1)

x_f_total = x_f_1 + x_f_2 + x_f_3 + x_f_4

x_t_total = ifft(x_f_total)*len(x_f_total)


In [3]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_1)), mode='lines', name=f'ch0 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_2)), mode='lines', name=f'ch1 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_3)), mode='lines', name=f'ch2 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_4)), mode='lines', name=f'ch3 content in x'))
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_total)), mode='lines', name=f'Combined Wide-band Signal (x)', line=dict(dash="dot")))    
fig.update_layout(width=700,height=400, title='Multi-Channel  Waveform', xaxis_title='Frequency Sample', yaxis_title='Magnitude (dB)',
                  xaxis_range=[0, 4000], yaxis_range=[-150, 10])

In [4]:
fig.write_html("wideband_signal.html",
               include_plotlyjs='cdn',
               full_html=False)

# Conventional Approach

In [5]:
import numpy as np
from scipy import signal
import matplotlib.pyplot as plt

num_taps = 64  # Number of filter taps (coefficients) - typically odd for linear phase

filter_taps = signal.firwin(num_taps, 0.25, pass_zero=True)

filter_freq_response = fft(filter_taps, 4000)

In [6]:
fig_filter = go.Figure()
fig_filter.add_trace(go.Scatter(y=filter_taps, mode='lines+markers', name=f'64-Tap Low-pass Filter'))   
fig_filter.update_layout(width=700,height=400, title='64-Tap Low-pass Filter', xaxis_title='Time Sample', yaxis_title='Magnitude (Linear)',
                  )

In [7]:
fig_filter.write_html("lpf_taps.html",
                        include_plotlyjs='cdn',
                        full_html=False)

In [8]:
### Apply frequency shift on channel 3
x_f_total_shifted = np.roll(x_f_total, -2000)
x_f_1_shifted = np.roll(x_f_1, -2000)
x_f_2_shifted = np.roll(x_f_2, -2000)
x_f_3_shifted = np.roll(x_f_3, -2000)
x_f_4_shifted = np.roll(x_f_4, -2000)

In [9]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_1_shifted)), mode='lines', name=f'ch0 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_2_shifted)), mode='lines', name=f'ch1 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_3_shifted)), mode='lines', name=f'ch2 content in x'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_4_shifted)), mode='lines', name=f'ch3 content in x'))
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_total_shifted)), mode='lines', name=f'Frequency-Shifted Wide-band Signal (x)', line=dict(dash="dot")))   
fig.update_layout(width=700,height=400, title='Frequency-Shifted Multi-Channel Waveform', xaxis_title='Frequency Sample', yaxis_title='Magnitude (dB)',
                  xaxis_range=[0, 4000], yaxis_range=[-150, 10])

In [10]:
fig.write_html("shifted_wideband_signal.html",
               include_plotlyjs='cdn',
               full_html=False)

In [11]:
# 4. Apply the filter to the signal
x_f_total_filtered = filter_freq_response*x_f_total_shifted
x_f_1_filtered = filter_freq_response*x_f_1_shifted
x_f_2_filtered = filter_freq_response*x_f_2_shifted
x_f_3_filtered = filter_freq_response*x_f_3_shifted
x_f_4_filtered = filter_freq_response*x_f_4_shifted

In [12]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_1_filtered)), mode='lines', name=f'ch0 content in x (filtered)'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_2_filtered)), mode='lines', name=f'ch1 content in x (filtered)'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_3_filtered)), mode='lines', name=f'ch2 content in x (filtered)'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_4_filtered)), mode='lines', name=f'ch3 content in x (filtered)'))
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_total_filtered)), mode='lines', name=f'Wide-band Signal x (Filtered)', line=dict(dash="dot")))   
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(filter_freq_response)), mode='lines', name=f'Filter Response', line=dict(dash="dot")))   
fig.update_layout(width=700,height=400, title='Filtered Multi-Channel Waveform', xaxis_title='Frequency Sample', yaxis_title='Magnitude (dB)',
                  xaxis_range=[0, 4000], yaxis_range=[-150, 10])

In [13]:
fig.write_html("filtered_wideband_signal.html",
               include_plotlyjs='cdn',
               full_html=False)

In [14]:
x_t_total_filtered = ifft(x_f_total_filtered)*len(x_f_total_filtered)
x_t_total_filtered_downsamp = x_t_total_filtered[::4]
x_f_total_filtered_downsamp = fft(x_t_total_filtered_downsamp)/len(x_t_total_filtered_downsamp)

In [15]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_total_filtered_downsamp)), mode='lines', name=f'ch3 (Extracted)'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_3_original)), mode='lines', name=f'ch3 (Original)'))    
fig.update_layout(width=700,height=400, title='ch3 Extracted by Decimation Filtering', xaxis_title='Frequency Sample', yaxis_title='Magnitude (dB)',
                  xaxis_range=[0, 1000], yaxis_range=[-150, 10])

In [16]:
fig.write_html("decim_filtered_signal.html",
               include_plotlyjs='cdn',
               full_html=False)

# Polyphase Channelizer

In [17]:
def plot_complex_spectrum(spectrum,
                           freq=None, 
                           name=f'Spectrum', 
                           fig=None, 
                           add_axis=False, 
                           plot_title=None, 
                           aspect_ratio=None, 
                           IQ_limit=1.5, 
                           scatter_mode='markers+lines',
                           color= None,
                           marker_size=2,
                           opacity=None,
                           line_width=None,
                           dash=None
                           ):
    if fig is None:
        fig = go.Figure()

    if freq is None:
        freq = np.arange(len(spectrum))
    fig.add_trace(go.Scatter3d(x=freq,
                                y=np.imag(spectrum),
                                z=np.real(spectrum),
                                mode=scatter_mode, name=name,
                                marker=dict(size=marker_size),
                                opacity=1))   
    
    if color is not None:
        fig.data[-1].marker.color = color
        fig.data[-1].line.color = color

    if opacity is not None:
        fig.data[-1].opacity = opacity

    if dash is not None:
        fig.data[-1].line.dash = dash

    if line_width is not None:
        fig.data[-1].line.width = line_width  

    fig.update_layout(width=700,height=650,
                        scene=dict(
                            xaxis=dict( title="Frequency"),
                            yaxis=dict(range=[-1, 1], title="Q"),
                            zaxis=dict(range=[-1, 1], title="I"),
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.75),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ),
                        legend=dict(
                                    orientation="h",          # horizontal
                                    yanchor="bottom",         # anchor legend to bottom
                                    y=0,                   # push legend below plot
                                    xanchor="center",         # anchor centered horizontally
                                    x=0.5
                                    ),
                        margin=dict(l=00, r=00, t=50, b=0)
                        )
    
    if aspect_ratio is not None:
        fig.update_layout(scene=dict(aspectmode="manual",           # allow manual control
                                     aspectratio=dict(x=aspect_ratio[0], 
                                                      y=aspect_ratio[1], 
                                                      z=aspect_ratio[2]),  # scale of each axis
                                     ))
    if plot_title is not None:
        fig.update_layout(title=plot_title)

    if IQ_limit is not None:
        fig.update_layout(scene=dict(yaxis=dict(range=[-IQ_limit, IQ_limit], title="Q"),
                                     zaxis=dict(range=[-IQ_limit, IQ_limit], title="I"),
                                     ))
    # plot axes
    if add_axis==True:
        fig.add_trace(go.Scatter3d(
            x=[0,len(spectrum)], y=[0,0], z=[0,0],
            mode="lines", line=dict(color="black", width=1),
            name="X=0 axis", showlegend=False
        ))

        fig.add_trace(go.Scatter3d(
            x=[0,0], y=[-IQ_limit,IQ_limit], z=[0,0],
            mode="lines", line=dict(color="black", width=1),
            name="X=0 axis", showlegend=False
        ))

        fig.add_trace(go.Scatter3d(
            x=[0,0], y=[0,0], z=[-IQ_limit,IQ_limit],
            mode="lines", line=dict(color="black", width=1),
            name="X=0 axis", showlegend=False
        ))

        fig.add_trace(go.Scatter3d(
            x=[len(spectrum),len(spectrum)], y=[-IQ_limit,IQ_limit], z=[0,0],
            mode="lines", line=dict(color="black", width=1),
            name="X=0 axis", showlegend=False
        ))

        fig.add_trace(go.Scatter3d(
            x=[len(spectrum),len(spectrum)], y=[0,0], z=[-IQ_limit,IQ_limit],
            mode="lines", line=dict(color="black", width=1),
            name="X=0 axis", showlegend=False
        ))

    # Draw Unity Circle
    theta = np.linspace(0, 2*np.pi, 200)

    # Parametric circle
    y_unity_circle = IQ_limit*np.cos(theta)
    z_unity_circle = IQ_limit*np.sin(theta)

    fig.add_trace(go.Scatter3d(
                    x=np.zeros(y_unity_circle.shape), 
                    y=y_unity_circle, 
                    z=z_unity_circle,
                    mode='lines',
                    line=dict(color="black", width=1),
                    showlegend=False
                    ))

    fig.add_trace(go.Scatter3d(
                    x=len(spectrum)*np.ones(y_unity_circle.shape), 
                    y=y_unity_circle, 
                    z=z_unity_circle,
                    mode='lines',
                    line=dict(color="black", width=1),
                    showlegend=False
                    ))
    
    return fig

In [18]:
def create_slider_fig(figs_list, labels_list, combined_plot_title="Combined Figure"):
    combined = go.Figure()

    # Add the first figure's traces as the initial data
    combined.add_traces(figs_list[0].data)

    # Build frames from all figs
    frames = []
    for i, f in enumerate(figs_list, start=1):
        frames.append(go.Frame(data=f.data, name=f"frame{i}"))

    combined.frames = frames

    # Add slider
    combined.update_layout(
        sliders=[{
            "steps": [
                {"args": [[f.name], {"frame": {"duration": 0}, "mode": "immediate"}],
                "label": labels_list[i], 
                "method": "animate"}
                for i, f in enumerate(combined.frames)
            ],
            "transition": {"duration": 0},
            "x": 0.1, "y": -0.1, "len": 0.9
        }],
        width=figs_list[0].layout['width'],
        height=figs_list[0].layout['height']+150,
        scene=figs_list[0].layout['scene'],
        title=combined_plot_title,
        legend=dict(
            orientation="h",          # horizontal
            yanchor="bottom",         # anchor legend to bottom
            y=0,                   # push legend below plot
            xanchor="center",         # anchor centered horizontally
            x=0.5
        )
        )
    return combined

# Test Polyphase Filter

In [19]:
num_taps = 64  # Number of filter taps (coefficients) - typically odd for linear phase
filter_taps = signal.firwin(num_taps, 0.25, pass_zero=True)

### Construct Ideal Filter
filter_freq_response = 0.00*np.ones(4000) + 0j
filter_freq_response[0:450] += 1
filter_freq_response[3550:] += 1
filter_taps = np.fft.ifft(filter_freq_response)*len(filter_freq_response)

In [20]:
fig_filter_freq = plot_complex_spectrum(filter_freq_response, 
                                         name='Ideal Low-pass Filter Frequency Response', 
                                         plot_title='Ideal Low-pass Filter Frequency Response', 
                                         scatter_mode='markers+lines',
                                         add_axis=True,
                                         IQ_limit=1.25,
                                         marker_size=2)
fig_filter_freq.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.5, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))

In [21]:
fig_filter_freq.write_html("ideal_lpf_spectrum.html",
                           include_plotlyjs='cdn',
                            full_html=False)

In [22]:
down_samp_mask = np.zeros(4000)
down_samp_mask[0::4] = 1


filter_f_0 = fft(np.roll(filter_taps,0)*down_samp_mask, 4000)/len(filter_taps)
filter_f_1 = fft(np.roll(filter_taps,1)*down_samp_mask, 4000)/len(filter_taps)
filter_f_2 = fft(np.roll(filter_taps,2)*down_samp_mask, 4000)/len(filter_taps)
filter_f_3 = fft(np.roll(filter_taps,3)*down_samp_mask, 4000)/len(filter_taps)

filter_f_0 = fft(signal.decimate(np.roll(filter_taps,0)*down_samp_mask,4, ftype='fir'), 1000)/1000*4
filter_f_1 = fft(signal.decimate(np.roll(filter_taps,1)*down_samp_mask,4, ftype='fir'), 1000)/1000*4
filter_f_2 = fft(signal.decimate(np.roll(filter_taps,2)*down_samp_mask,4, ftype='fir'), 1000)/1000*4
filter_f_3 = fft(signal.decimate(np.roll(filter_taps,3)*down_samp_mask,4, ftype='fir'), 1000)/1000*4

In [23]:
fig_filter_downsamp = plot_complex_spectrum(filter_f_0, name='Spectrum of h0', add_axis=True, IQ_limit=1.25, plot_title="Frequency Response of Down-sampled Filters")
fig_filter_downsamp = plot_complex_spectrum(filter_f_1, name='Spectrum of h1', add_axis=True, IQ_limit=1.25, plot_title="Frequency Response of Down-sampled Filters", fig = fig_filter_downsamp)
fig_filter_downsamp = plot_complex_spectrum(filter_f_2, name='Spectrum of h2', add_axis=True, IQ_limit=1.25, plot_title="Frequency Response of Down-sampled Filters", fig = fig_filter_downsamp)
fig_filter_downsamp = plot_complex_spectrum(filter_f_3, name='Spectrum of h3', add_axis=True, IQ_limit=1.25, plot_title="Frequency Response of Down-sampled Filters", fig = fig_filter_downsamp)

fig_filter_downsamp.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.5, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))
fig_filter_downsamp.show()

In [24]:
fig_filter_downsamp.write_html("downsampled_filter_spectrum.html",
                                include_plotlyjs='cdn',
                                full_html=False)

In [25]:
x_f_0 = np.ones(1000) + 0j
x_f_0[100:900] *= 1e-6
x_t_0 = ifft(x_f_0)*len(x_f_0)
x_t_0 = resample(x_t_0, 4000)
x_f_0 = fft(x_t_0)/len(x_t_0)

x_f_1 = np.ones(1000) + 0j
x_f_1[200:800] *= 1e-6
x_t_1 = ifft(x_f_1)*len(x_f_1)
x_t_1 = resample(x_t_1, 4000)
x_t_1 *= np.exp(1j*2*np.pi*1000*np.arange(len(x_t_1))/4000)
x_f_1 = fft(x_t_1)/len(x_t_1)

x_f_2 = np.ones(1000) + 0j
x_f_2[300:700] *= 1e-6
x_t_2 = ifft(x_f_2)*len(x_f_2)
x_t_2 = resample(x_t_2, 4000)
x_t_2 *= np.exp(1j*2*np.pi*2000*np.arange(len(x_t_2))/4000)
x_f_2 = fft(x_t_2)/len(x_t_2)

x_f_3 = np.ones(1000) + 0j
x_f_3[400:600] *= 1e-6
x_t_3 = ifft(x_f_3)*len(x_f_3)
x_t_3 = resample(x_t_3, 4000)
x_t_3 *= np.exp(1j*2*np.pi*3000*np.arange(len(x_t_3))/4000)
x_f_3 = fft(x_t_3)/len(x_t_3)

x_f_total = x_f_0 + x_f_1 + x_f_2 + x_f_3
x_t_total = ifft(x_f_total)*len(x_f_total)

In [26]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_0)), mode='lines', name=f'ch 0 component'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_1)), mode='lines', name=f'ch 1 component'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_2)), mode='lines', name=f'ch 2 component'))    
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_3)), mode='lines', name=f'ch 3 component'))
fig.add_trace(go.Scatter(y=20*np.log10(np.abs(x_f_total)), mode='lines', name=f'Combined Wide-band Signal', line=dict(dash="dot")))    
fig.update_layout(width=700,height=400, title='Multi-Channel Input Waveform', xaxis_title='Frequency', yaxis_title='Magnitude (dB)',
                  xaxis_range=[0, 4000], yaxis_range=[-150, 10])



In [27]:
fig.write_html("wideband_signal_polyphase_input.html",
               include_plotlyjs='cdn',
               full_html=False)

In [28]:
fig_complex_input_spectrum = plot_complex_spectrum(x_f_0, name='ch 0 component', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_complex_input_spectrum = plot_complex_spectrum(x_f_1, name='ch 1 component', add_axis=True, IQ_limit=1.25, fig=fig_complex_input_spectrum)
fig_complex_input_spectrum = plot_complex_spectrum(x_f_2, name='ch 2 component', add_axis=True, IQ_limit=1.25, fig=fig_complex_input_spectrum)
fig_complex_input_spectrum = plot_complex_spectrum(x_f_3, name='ch 3 component', add_axis=True, IQ_limit=1.25, fig=fig_complex_input_spectrum)
fig_complex_input_spectrum.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.5, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  

In [29]:
fig_complex_input_spectrum.write_html("complex_spectrum_wideband_input.html",
                                        include_plotlyjs='cdn',
                                        full_html=False)

In [30]:
### Check filtering with decimation
y_filt_f = x_f_total*fft(filter_taps, n=len(x_f_total))
x_filt_t = ifft(y_filt_f)*len(y_filt_f)
x_filt_downsamp_t = x_filt_t[0::4]
x_filt_downsamp_f = fft(x_filt_downsamp_t)/len(x_filt_downsamp_t)


In [31]:
x_t_total_delay0_downsamp = x_t_total[0::4]
x_t_0_delay0_downsamp = x_t_0[0::4]
x_t_1_delay0_downsamp = x_t_1[0::4]
x_t_2_delay0_downsamp = x_t_2[0::4]
x_t_3_delay0_downsamp = x_t_3[0::4]

x_f_total_delay0_downsamp = fft(x_t_total_delay0_downsamp)/len(x_t_total_delay0_downsamp)
x_f_0_delay0_downsamp = fft(x_t_0_delay0_downsamp)/len(x_t_0_delay0_downsamp)
x_f_1_delay0_downsamp = fft(x_t_1_delay0_downsamp)/len(x_t_1_delay0_downsamp)
x_f_2_delay0_downsamp = fft(x_t_2_delay0_downsamp)/len(x_t_2_delay0_downsamp)
x_f_3_delay0_downsamp = fft(x_t_3_delay0_downsamp)/len(x_t_3_delay0_downsamp)


x_t_total_delay1_downsamp = x_t_total[1::4]
x_t_0_delay1_downsamp = x_t_0[1::4]
x_t_1_delay1_downsamp = x_t_1[1::4]
x_t_2_delay1_downsamp = x_t_2[1::4]
x_t_3_delay1_downsamp = x_t_3[1::4]
x_f_total_delay1_downsamp = fft(x_t_total_delay1_downsamp)/len(x_t_total_delay1_downsamp)
x_f_0_delay1_downsamp = fft(x_t_0_delay1_downsamp)/len(x_t_0_delay1_downsamp)
x_f_1_delay1_downsamp = fft(x_t_1_delay1_downsamp)/len(x_t_1_delay1_downsamp)
x_f_2_delay1_downsamp = fft(x_t_2_delay1_downsamp)/len(x_t_2_delay1_downsamp)
x_f_3_delay1_downsamp = fft(x_t_3_delay1_downsamp)/len(x_t_3_delay1_downsamp)


x_t_total_delay2_downsamp = x_t_total[2::4]
x_t_0_delay2_downsamp = x_t_0[2::4]
x_t_1_delay2_downsamp = x_t_1[2::4]
x_t_2_delay2_downsamp = x_t_2[2::4]
x_t_3_delay2_downsamp = x_t_3[2::4]
x_f_total_delay2_downsamp = fft(x_t_total_delay2_downsamp)/len(x_t_total_delay2_downsamp)
x_f_0_delay2_downsamp = fft(x_t_0_delay2_downsamp)/len(x_t_0_delay2_downsamp)
x_f_1_delay2_downsamp = fft(x_t_1_delay2_downsamp)/len(x_t_1_delay2_downsamp)
x_f_2_delay2_downsamp = fft(x_t_2_delay2_downsamp)/len(x_t_2_delay2_downsamp)
x_f_3_delay2_downsamp = fft(x_t_3_delay2_downsamp)/len(x_t_3_delay2_downsamp)


x_t_total_delay3_downsamp = x_t_total[3::4]
x_t_0_delay3_downsamp = x_t_0[3::4]
x_t_1_delay3_downsamp = x_t_1[3::4]
x_t_2_delay3_downsamp = x_t_2[3::4]
x_t_3_delay3_downsamp = x_t_3[3::4]
x_f_total_delay3_downsamp = fft(x_t_total_delay3_downsamp)/len(x_t_total_delay3_downsamp)
x_f_0_delay3_downsamp = fft(x_t_0_delay3_downsamp)/len(x_t_0_delay3_downsamp)
x_f_1_delay3_downsamp = fft(x_t_1_delay3_downsamp)/len(x_t_1_delay3_downsamp)
x_f_2_delay3_downsamp = fft(x_t_2_delay3_downsamp)/len(x_t_2_delay3_downsamp)
x_f_3_delay3_downsamp = fft(x_t_3_delay3_downsamp)/len(x_t_3_delay3_downsamp)

In [207]:
fig_stream0 = plot_complex_spectrum(x_f_0_delay0_downsamp, name='ch 0 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 0 (delay=0) Spectrum")
fig_stream0 = plot_complex_spectrum(x_f_1_delay0_downsamp, name='ch 1 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 0 (delay=0) Spectrum", fig=fig_stream0)
fig_stream0 = plot_complex_spectrum(x_f_2_delay0_downsamp, name='ch 2 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 0 (delay=0) Spectrum", fig=fig_stream0)
fig_stream0 = plot_complex_spectrum(x_f_3_delay0_downsamp, name='ch 3 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 0 (delay=0) Spectrum", fig=fig_stream0)
# fig_stream0.show()

fig_stream1 = plot_complex_spectrum(x_f_0_delay1_downsamp, name='ch 0 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 1 (delay=1) Spectrum")
fig_stream1 = plot_complex_spectrum(x_f_1_delay1_downsamp, name='ch 1 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 1 (delay=1) Spectrum", fig=fig_stream1)
fig_stream1 = plot_complex_spectrum(x_f_2_delay1_downsamp, name='ch 2 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 1 (delay=1) Spectrum", fig=fig_stream1)
fig_stream1 = plot_complex_spectrum(x_f_3_delay1_downsamp, name='ch 3 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 1 (delay=1) Spectrum", fig=fig_stream1)
# fig_stream1.show()

fig_stream2 = plot_complex_spectrum(x_f_0_delay2_downsamp, name='ch 0 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 2 (delay=2) Spectrum")
fig_stream2 = plot_complex_spectrum(x_f_1_delay2_downsamp, name='ch 1 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 2 (delay=2) Spectrum", fig=fig_stream2)
fig_stream2 = plot_complex_spectrum(x_f_2_delay2_downsamp, name='ch 2 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 2 (delay=2) Spectrum", fig=fig_stream2)
fig_stream2 = plot_complex_spectrum(x_f_3_delay2_downsamp, name='ch 3 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 2 (delay=2) Spectrum", fig=fig_stream2)
# fig_stream2.show()

fig_stream3 = plot_complex_spectrum(x_f_0_delay3_downsamp, name='ch 0 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 3 (delay=3) Spectrum")
fig_stream3 = plot_complex_spectrum(x_f_1_delay3_downsamp, name='ch 1 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 3 (delay=3) Spectrum", fig=fig_stream3)
fig_stream3 = plot_complex_spectrum(x_f_2_delay3_downsamp, name='ch 2 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 3 (delay=3) Spectrum", fig=fig_stream3)
fig_stream3 = plot_complex_spectrum(x_f_3_delay3_downsamp, name='ch 3 component', add_axis=True, IQ_limit=1.25, plot_title="Down-sampled Stream 3 (delay=3) Spectrum", fig=fig_stream3)
# fig_stream3.show()

fig_streams = create_slider_fig([fig_stream0, fig_stream1, fig_stream2, fig_stream3],
                                ['x0', 'x1', 'x2', 'x3'],
                                combined_plot_title="Complex Spectra of Down-sampled Input Streams")

fig_streams.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible

In [33]:
fig_streams.write_html("downsampled_streams_spectrum.html",
                       include_plotlyjs='cdn',
                          full_html=False)

In [34]:
filter_0_t = filter_taps[0::4]
filter_1_t = filter_taps[1::4]
filter_2_t = filter_taps[2::4]
filter_3_t = filter_taps[3::4]

filter_0_f = fft(filter_0_t,1000)
filter_1_f = fft(filter_1_t,1000)
filter_2_f = fft(filter_2_t,1000)
filter_3_f = fft(filter_3_t,1000)

In [35]:
y0 = ifft(x_f_total_delay0_downsamp*filter_0_f)
y0_ch0_f = x_f_0_delay0_downsamp*filter_0_f/1000
y0_ch1_f = x_f_1_delay0_downsamp*filter_0_f/1000
y0_ch2_f = x_f_2_delay0_downsamp*filter_0_f/1000
y0_ch3_f = x_f_3_delay0_downsamp*filter_0_f/1000
y0_ch0_t = ifft(y0_ch0_f)*1000
y0_ch1_t = ifft(y0_ch1_f)*1000
y0_ch2_t = ifft(y0_ch2_f)*1000
y0_ch3_t = ifft(y0_ch3_f)*1000


y1 = ifft(x_f_total_delay3_downsamp*filter_1_f)
y1_ch0_f = x_f_0_delay3_downsamp*filter_1_f/1000
y1_ch1_f = x_f_1_delay3_downsamp*filter_1_f/1000
y1_ch2_f = x_f_2_delay3_downsamp*filter_1_f/1000
y1_ch3_f = x_f_3_delay3_downsamp*filter_1_f/1000
y1_ch0_t = ifft(y1_ch0_f)*1000
y1_ch1_t = ifft(y1_ch1_f)*1000
y1_ch2_t = ifft(y1_ch2_f)*1000
y1_ch3_t = ifft(y1_ch3_f)*1000



y2 = ifft(x_f_total_delay2_downsamp*filter_2_f)
y2_ch0_f = x_f_0_delay2_downsamp*filter_2_f/1000
y2_ch1_f = x_f_1_delay2_downsamp*filter_2_f/1000
y2_ch2_f = x_f_2_delay2_downsamp*filter_2_f/1000
y2_ch3_f = x_f_3_delay2_downsamp*filter_2_f/1000
y2_ch0_t = ifft(y2_ch0_f)*1000
y2_ch1_t = ifft(y2_ch1_f)*1000
y2_ch2_t = ifft(y2_ch2_f)*1000
y2_ch3_t = ifft(y2_ch3_f)*1000



y3 = ifft(x_f_total_delay1_downsamp*filter_3_f)
y3_ch0_f = x_f_0_delay1_downsamp*filter_3_f/1000
y3_ch1_f = x_f_1_delay1_downsamp*filter_3_f/1000
y3_ch2_f = x_f_2_delay1_downsamp*filter_3_f/1000
y3_ch3_f = x_f_3_delay1_downsamp*filter_3_f/1000
y3_ch0_t = ifft(y3_ch0_f)
y3_ch1_t = ifft(y3_ch1_f)
y3_ch2_t = ifft(y3_ch2_f)
y3_ch3_t = ifft(y3_ch3_f)



y_out_t_ch0 = np.roll(y0, 0) + np.roll(y1, 1)  + np.roll(y2, 1)  + np.roll(y3, 1)
y_out_t_ch1 = np.roll(y0, 0) + 1j*np.roll(y1, 1)  + -1*np.roll(y2, 1)  + -1j*np.roll(y3, 1)
y_out_t_ch2 = np.roll(y0, 0) + -1*np.roll(y1, 1)  + np.roll(y2, 1)  + -1*np.roll(y3, 1)
y_out_t_ch3 = np.roll(y0, 0) + -1j*np.roll(y1, 1)  + -1*np.roll(y2, 1)  + 1j*np.roll(y3, 1)

y_out_f_ch0 = fft(y_out_t_ch0)/len(y_out_t_ch0)
y_out_f_ch1 = fft(y_out_t_ch1)/len(y_out_t_ch1)
y_out_f_ch2 = fft(y_out_t_ch2)/len(y_out_t_ch2)
y_out_f_ch3 = fft(y_out_t_ch3)/len(y_out_t_ch3)

# Combined Filtered Output

In [36]:
'#636EFA'
'#EF553B'
'#00CC96'
'#AB63FA'
'#FFA15A'
'#19D3F3'
'#FF6692'
'#B6E880'
'#FF97EF'
'#FECB52'

'#FECB52'

In [37]:
fig_ch0 = plot_complex_spectrum(x_f_0_delay0_downsamp, name='Ch0 in x0', add_axis=True, IQ_limit=1.25, color='#636EFA')
fig_ch0 = plot_complex_spectrum(x_f_0_delay1_downsamp, name='Ch0 in x1', add_axis=True, IQ_limit=1.25, color='#EF553B',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(x_f_0_delay2_downsamp, name='Ch0 in x2', add_axis=True, IQ_limit=1.25, color='#00CC96',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(x_f_0_delay3_downsamp, name='Ch0 in x3', add_axis=True, IQ_limit=1.25, color='#AB63FA',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(filter_0_f/1000, name='h0', add_axis=True, IQ_limit=1.25, color='#636EFA', scatter_mode='lines',dash='dot',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(filter_3_f/1000, name='h3', add_axis=True, IQ_limit=1.25, color='#EF553B', scatter_mode='lines',dash='dot',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(filter_2_f/1000, name='h2', add_axis=True, IQ_limit=1.25, color='#00CC96', scatter_mode='lines',dash='dot',fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(filter_1_f/1000, name='h1', add_axis=True, IQ_limit=1.25, color='#AB63FA', scatter_mode='lines',dash='dot',fig =fig_ch0)

fig_ch0 = plot_complex_spectrum(x_f_0_delay0_downsamp*filter_0_f/1000, name='Ch0 in x0*h0', add_axis=True, IQ_limit=1.25, color='#636EFA',scatter_mode='lines',line_width=3,fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(x_f_0_delay1_downsamp*filter_3_f/1000, name='Ch0 in x1*h3', add_axis=True, IQ_limit=1.25, color='#EF553B',scatter_mode='lines',line_width=3,fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(x_f_0_delay2_downsamp*filter_2_f/1000, name='Ch0 in x2*h2', add_axis=True, IQ_limit=1.25, color='#00CC96',scatter_mode='lines',line_width=3,fig =fig_ch0)
fig_ch0 = plot_complex_spectrum(x_f_0_delay3_downsamp*filter_1_f/1000, name='Ch0 in x3*h1', add_axis=True, IQ_limit=1.25, color='#AB63FA',scatter_mode='lines',line_width=3,fig =fig_ch0)

# *np.exp(-1j*2*np.pi*np.arange(1000)/1000)
# fig_ch0.show()

fig_ch1 = plot_complex_spectrum(x_f_1_delay0_downsamp, name='Ch1 in x0', add_axis=True, IQ_limit=1.25, color='#636EFA')
fig_ch1 = plot_complex_spectrum(x_f_1_delay1_downsamp, name='Ch1 in x1', add_axis=True, IQ_limit=1.25, color='#EF553B',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay2_downsamp, name='Ch1 in x2', add_axis=True, IQ_limit=1.25, color='#00CC96',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay3_downsamp, name='Ch1 in x3', add_axis=True, IQ_limit=1.25, color='#AB63FA',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(filter_0_f/1000, name='h0', add_axis=True, IQ_limit=1.25, color='#636EFA', scatter_mode='lines',dash='dot',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(filter_3_f/1000, name='h3', add_axis=True, IQ_limit=1.25, color='#EF553B', scatter_mode='lines',dash='dot',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(filter_2_f/1000, name='h2', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input", color='#00CC96', scatter_mode='lines',dash='dot',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(filter_1_f/1000, name='h1', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input", color='#AB63FA', scatter_mode='lines',dash='dot',fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay0_downsamp*filter_0_f/1000, name='Ch1 in x0*h0', add_axis=True, IQ_limit=1.25, color='#636EFA',scatter_mode='lines',line_width=3,fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay1_downsamp*filter_3_f/1000, name='Ch1 in x1*h3', add_axis=True, IQ_limit=1.25, color='#EF553B',scatter_mode='lines',line_width=3,fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay2_downsamp*filter_2_f/1000, name='Ch1 in x2*h2', add_axis=True, IQ_limit=1.25, color='#00CC96',scatter_mode='lines',line_width=3,fig =fig_ch1)
fig_ch1 = plot_complex_spectrum(x_f_1_delay3_downsamp*filter_1_f/1000, name='Ch1 in x3*h1', add_axis=True, IQ_limit=1.25, color='#AB63FA',scatter_mode='lines',line_width=3,fig =fig_ch1)
# fig_ch1.show()

fig_ch2 = plot_complex_spectrum(x_f_2_delay0_downsamp, name='Ch2 in x0', add_axis=True, IQ_limit=1.25, color='#636EFA')
fig_ch2 = plot_complex_spectrum(x_f_2_delay1_downsamp, name='Ch2 in x1', add_axis=True, IQ_limit=1.25, color='#EF553B',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay2_downsamp, name='Ch2 in x2', add_axis=True, IQ_limit=1.25, color='#00CC96',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay3_downsamp, name='Ch2 in x3', add_axis=True, IQ_limit=1.25, color='#AB63FA',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(filter_0_f/1000, name='h0', add_axis=True, IQ_limit=1.25, color='#636EFA', scatter_mode='lines',dash='dot',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(filter_3_f/1000, name='h3', add_axis=True, IQ_limit=1.25, color='#EF553B', scatter_mode='lines',dash='dot',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(filter_2_f/1000, name='h2', add_axis=True, IQ_limit=1.25, color='#00CC96', scatter_mode='lines',dash='dot',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(filter_1_f/1000, name='h1', add_axis=True, IQ_limit=1.25, color='#AB63FA', scatter_mode='lines',dash='dot',fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay0_downsamp*filter_0_f/1000, name='Ch2 in x0*h0', add_axis=True, IQ_limit=1.25, color='#636EFA',scatter_mode='lines',line_width=3,fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay1_downsamp*filter_3_f/1000, name='Ch2 in x1*h3', add_axis=True, IQ_limit=1.25, color='#EF553B',scatter_mode='lines',line_width=3,fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay2_downsamp*filter_2_f/1000, name='Ch2 in x2*h2', add_axis=True, IQ_limit=1.25, color='#00CC96',scatter_mode='lines',line_width=3,fig =fig_ch2)
fig_ch2 = plot_complex_spectrum(x_f_2_delay3_downsamp*filter_1_f/1000, name='Ch2 in x3*h1', add_axis=True, IQ_limit=1.25, color='#AB63FA',scatter_mode='lines',line_width=3,fig =fig_ch2)
# fig_ch2.show()

fig_ch3 = plot_complex_spectrum(x_f_3_delay0_downsamp, name='Ch3 in x0', add_axis=True, IQ_limit=1.25, color='#636EFA')
fig_ch3 = plot_complex_spectrum(x_f_3_delay1_downsamp, name='Ch3 in x1', add_axis=True, IQ_limit=1.25, color='#EF553B',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay2_downsamp, name='Ch3 in x2', add_axis=True, IQ_limit=1.25, color='#00CC96',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay3_downsamp, name='Ch3 in x3', add_axis=True, IQ_limit=1.25, color='#AB63FA',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(filter_0_f/1000, name='h0', add_axis=True, IQ_limit=1.25, color='#636EFA', scatter_mode='lines',dash='dot',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(filter_3_f/1000, name='h3', add_axis=True, IQ_limit=1.25, color='#EF553B', scatter_mode='lines',dash='dot',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(filter_2_f/1000, name='h2', add_axis=True, IQ_limit=1.25, color='#00CC96', scatter_mode='lines',dash='dot',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(filter_1_f/1000, name='h1', add_axis=True, IQ_limit=1.25, color='#AB63FA', scatter_mode='lines',dash='dot',fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay0_downsamp*filter_0_f/1000, name='Ch3 in x0*h0', add_axis=True, IQ_limit=1.25, color='#636EFA',scatter_mode='lines',line_width=3,fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay1_downsamp*filter_3_f/1000, name='Ch3 in x1*h3', add_axis=True, IQ_limit=1.25, color='#EF553B',scatter_mode='lines',line_width=3,fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay2_downsamp*filter_2_f/1000, name='Ch3 in x2*h2', add_axis=True, IQ_limit=1.25, color='#00CC96',scatter_mode='lines',line_width=3,fig =fig_ch3)
fig_ch3 = plot_complex_spectrum(x_f_3_delay3_downsamp*filter_1_f/1000, name='Ch3 in x3*h1', add_axis=True, IQ_limit=1.25, color='#AB63FA',scatter_mode='lines',line_width=3,fig =fig_ch3)
# fig_ch3.show()

fig_filter_bank_input = create_slider_fig([fig_ch0, fig_ch1, fig_ch2, fig_ch3],
                                ['Channel 1', 'Channel 2', 'Channel 3', 'Channel 4'],
                                combined_plot_title="Inputs to Polyphase Filter Bank")

fig_filter_bank_input.update_layout(width=700, height=600,
                                    scene=dict(
                                      aspectmode="manual",           # allow manual control
                                      aspectratio=dict(x=1.5, y=0.5, z=0.5),  # scale of each axis
                                      camera=dict(eye=dict(x=-1.25, y=-1.5, z=0.55),
                                                  up=dict(x=0, y=0, z=1),
                                                  center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                                  ))  # adjust the camera so labels are visible


In [38]:
fig_filter_bank_input.write_html("filter_bank_input.html",
                                 include_plotlyjs='cdn',
                                 full_html=False,)


In [39]:
fig_output_0 = plot_complex_spectrum(y0_ch0_f, name='h0 Output', add_axis=True, IQ_limit=1.25,color='#636EFA', plot_title="Complex Spectrum of Wide-band Input",)
fig_output_0 = plot_complex_spectrum(y1_ch0_f, name='h1 Output', add_axis=True, IQ_limit=1.25,color='#EF553B', fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(y2_ch0_f, name='h2 Output', add_axis=True, IQ_limit=1.25,color='#00CC96', fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(y3_ch0_f, name='h3 Output', add_axis=True, IQ_limit=1.25,color='#AB63FA', fig=fig_output_0)
# fig_output_0.show()


fig_output_1 = plot_complex_spectrum(y0_ch1_f, name='h0 Output', add_axis=True, IQ_limit=1.25,color='#636EFA', plot_title="Complex Spectrum of Wide-band Input",)
fig_output_1 = plot_complex_spectrum(y1_ch1_f, name='h1 Output', add_axis=True, IQ_limit=1.25,color='#EF553B', fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(y2_ch1_f, name='h2 Output', add_axis=True, IQ_limit=1.25,color='#00CC96', fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(y3_ch1_f, name='h3 Output', add_axis=True, IQ_limit=1.25,color='#AB63FA', fig=fig_output_1)
# fig_output_1.show()


fig_output_2 = plot_complex_spectrum(y0_ch2_f, name='h0 Output', add_axis=True, IQ_limit=1.25,color='#636EFA', plot_title="Complex Spectrum of Wide-band Input",)
fig_output_2 = plot_complex_spectrum(y1_ch2_f, name='h1 Output', add_axis=True, IQ_limit=1.25,color='#EF553B', fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(y2_ch2_f, name='h2 Output', add_axis=True, IQ_limit=1.25,color='#00CC96', fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(y3_ch2_f, name='h3 Output', add_axis=True, IQ_limit=1.25,color='#AB63FA', fig=fig_output_2)
# fig_output_2.show()


fig_output_3 = plot_complex_spectrum(y0_ch3_f, name='h0 Output', add_axis=True, IQ_limit=1.25,color='#636EFA', plot_title="Complex Spectrum of Wide-band Input",)
fig_output_3 = plot_complex_spectrum(y1_ch3_f, name='h1 Output', add_axis=True, IQ_limit=1.25,color='#EF553B', fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(y2_ch3_f, name='h2 Output', add_axis=True, IQ_limit=1.25,color='#00CC96', fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(y3_ch3_f, name='h3 Output', add_axis=True, IQ_limit=1.25,color='#AB63FA', fig=fig_output_3)
# fig_output_3.show()

fig_filter_bank_output = create_slider_fig([fig_output_0, fig_output_1, fig_output_2, fig_output_3],
                                ['Ch 0 Component', 'Ch 1 Component', 'Ch 2 Component', 'Ch 3 Component'],
                                combined_plot_title="Polyphase Filter Bank Output")

fig_filter_bank_output.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible

In [40]:
fig_filter_bank_output.write_html("filter_bank_output.html",
                                 include_plotlyjs='cdn',
                                 full_html=False,)

In [41]:
fig_output_0 = plot_complex_spectrum(y0_ch0_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_0 = plot_complex_spectrum(y1_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(y2_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(y3_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
# fig_output_0.show()


fig_output_1 = plot_complex_spectrum(y0_ch1_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_1 = plot_complex_spectrum(y1_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(y2_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(y3_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
# fig_output_1.show()


fig_output_2 = plot_complex_spectrum(y0_ch2_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_2 = plot_complex_spectrum(y1_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(y2_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(y3_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
# fig_output_2.show()


fig_output_3 = plot_complex_spectrum(y0_ch3_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_3 = plot_complex_spectrum(y1_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(y2_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(y3_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
# fig_output_3.show()

fig_filter_bank_output_delayed_ch0 = create_slider_fig([fig_output_0, fig_output_1, fig_output_2, fig_output_3],
                                ['Ch 0 Component', 'Ch 1 Component', 'Ch 2 Component', 'Ch 3 Component'],
                                combined_plot_title="Polyphase Filter Bank Outputs (with Delay)")

fig_filter_bank_output_delayed_ch0.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible 

In [42]:
fig_filter_bank_output_delayed_ch0.write_html("filter_bank_output_delayed.html",
                                 include_plotlyjs='cdn',
                                 full_html=False,)

# Extracting Other Channels

In [43]:
fig_output_0 = plot_complex_spectrum(y0_ch0_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_0 = plot_complex_spectrum(1j*y1_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(-1*y2_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(-1j*y3_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
# fig_output_0.show()


fig_output_1 = plot_complex_spectrum(y0_ch1_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_1 = plot_complex_spectrum(1j*y1_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(-1*y2_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(-1j*y3_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
# fig_output_1.show()


fig_output_2 = plot_complex_spectrum(y0_ch2_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_2 = plot_complex_spectrum(1j*y1_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(-1*y2_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(-1j*y3_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
# fig_output_2.show()


fig_output_3 = plot_complex_spectrum(y0_ch3_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_3 = plot_complex_spectrum(1j*y1_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(-1*y2_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(-1j*y3_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
# fig_output_3.show()

fig_filter_bank_output_delayed_ch1 = create_slider_fig([fig_output_0, fig_output_1, fig_output_2, fig_output_3],
                                ['Ch 0 Component', 'Ch 1 Component', 'Ch 2 Component', 'Ch 3 Component'],
                                combined_plot_title="Polyphase Channelizer Output (y1)")

fig_filter_bank_output_delayed_ch1.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible 

fig_filter_bank_output_delayed_ch1.write_html("filter_bank_output_delayed_ch1.html",
                                              include_plotlyjs='cdn',
                                              full_html=False,)

In [44]:
fig_output_0 = plot_complex_spectrum(y0_ch0_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_0 = plot_complex_spectrum(-1*y1_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(y2_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(-1*y3_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
# fig_output_0.show()


fig_output_1 = plot_complex_spectrum(y0_ch1_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_1 = plot_complex_spectrum(-1*y1_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(y2_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(-1*y3_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
# fig_output_1.show()


fig_output_2 = plot_complex_spectrum(y0_ch2_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_2 = plot_complex_spectrum(-1*y1_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(y2_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(-1*y3_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
# fig_output_2.show()


fig_output_3 = plot_complex_spectrum(y0_ch3_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_3 = plot_complex_spectrum(-1*y1_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(y2_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(-1*y3_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
# fig_output_3.show()

fig_filter_bank_output_delayed_ch2 = create_slider_fig([fig_output_0, fig_output_1, fig_output_2, fig_output_3],
                                ['Ch 0 Component', 'Ch 1 Component', 'Ch 2 Component', 'Ch 3 Component'],
                                combined_plot_title="Polyphase Channelizer Output (y2)")

fig_filter_bank_output_delayed_ch2.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible 

fig_filter_bank_output_delayed_ch2.write_html("filter_bank_output_delayed_ch2.html",
                                              include_plotlyjs='cdn',
                                              full_html=False,)

In [45]:
fig_output_0 = plot_complex_spectrum(y0_ch0_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_0 = plot_complex_spectrum(-1j*y1_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(-1*y2_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
fig_output_0 = plot_complex_spectrum(1j*y3_ch0_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_0)
# fig_output_0.show()


fig_output_1 = plot_complex_spectrum(y0_ch1_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_1 = plot_complex_spectrum(-1j*y1_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(-1*y2_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
fig_output_1 = plot_complex_spectrum(1j*y3_ch1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_1)
# fig_output_1.show()


fig_output_2 = plot_complex_spectrum(y0_ch2_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_2 = plot_complex_spectrum(-1j*y1_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(-1*y2_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
fig_output_2 = plot_complex_spectrum(1j*y3_ch2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_2)
# fig_output_2.show()


fig_output_3 = plot_complex_spectrum(y0_ch3_f, name='h0 Out (0 delay)', add_axis=True, IQ_limit=1.25, plot_title="Complex Spectrum of Wide-band Input",)
fig_output_3 = plot_complex_spectrum(-1j*y1_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h1 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(-1*y2_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h2 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
fig_output_3 = plot_complex_spectrum(1j*y3_ch3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='h3 Out (1 delay)', add_axis=True, IQ_limit=1.25, fig=fig_output_3)
# fig_output_3.show()

fig_filter_bank_output_delayed_ch3 = create_slider_fig([fig_output_0, fig_output_1, fig_output_2, fig_output_3],
                                ['Ch 0 Component', 'Ch 1 Component', 'Ch 2 Component', 'Ch 3 Component'],
                                combined_plot_title="Polyphase Channelizer Output (y3)")

fig_filter_bank_output_delayed_ch3.update_layout(width=800, height=600,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.75, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))  # adjust the camera so labels are visible 

fig_filter_bank_output_delayed_ch3.write_html("filter_bank_output_delayed_ch3.html",
                                              include_plotlyjs='cdn',
                                              full_html=False,)

# Non-ideal Filter

In [195]:
x_f_0 = np.ones(1000) + 0j
x_f_0[100:900] *= 1e-6
x_t_0 = ifft(x_f_0)*len(x_f_0)
x_t_0 = resample(x_t_0, 4000)
x_f_0 = fft(x_t_0)/len(x_t_0)

In [196]:
### Construct Non-Ideal Filter
filter_freq_response = 1e-9*np.ones(4000) + 0j
filter_freq_response[0:450] += 1
filter_freq_response[3550:] += 1
filter_freq_response[450:2000] += 1 - np.linspace(1, 1550,1550)/1550
filter_freq_response[2000:3550] += np.linspace(1, 1550,1550)/1550
filter_taps = np.fft.ifft(filter_freq_response)*len(filter_freq_response)

In [197]:
fig_nonideal_filter_freq = plot_complex_spectrum(filter_freq_response, 
                                         name='Non-ideal LPF', 
                                         plot_title='Non-ideal Low-pass Filter Frequency Response', 
                                         scatter_mode='markers+lines',
                                         add_axis=True,
                                         IQ_limit=1.25,
                                         marker_size=2,
                                         color='#636EFA')

fig_nonideal_filter_freq = plot_complex_spectrum(x_f_0, 
                                         name='Input Signal', 
                                         plot_title='Non-ideal Low-pass Filter Frequency Response', 
                                         scatter_mode='markers+lines',
                                         add_axis=True,
                                         IQ_limit=1.25,
                                         marker_size=2,
                                         color='#EF553B',
                                         fig=fig_nonideal_filter_freq)

fig_nonideal_filter_freq = plot_complex_spectrum(filter_freq_response*x_f_0, 
                                         name='Output Signal', 
                                         plot_title='Non-ideal Low-pass Filter Acting on Narrow-band Input', 
                                         scatter_mode='markers+lines',
                                         add_axis=True,
                                         IQ_limit=1.25,
                                         marker_size=2,
                                         color='#00CC96',
                                         fig=fig_nonideal_filter_freq)

fig_nonideal_filter_freq.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.5, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))

In [198]:
fig_nonideal_filter_freq.write_html("nonideal_filter_freq.html",
                                    include_plotlyjs='cdn',
                                    full_html=False,)

In [189]:
x = x_t_0
h = filter_taps

y_filt_down = ifft((fft(x)/4000)*(fft(h)/4000))*4000
y_filt_down = y_filt_down[0::4]

h0 = h[0::4]
h1 = h[1::4]
h2 = h[2::4]
h3 = h[3::4]

h0_f = fft(h0)/len(h0)
h1_f = fft(h1)/len(h1)
h2_f = fft(h2)/len(h2)
h3_f = fft(h3)/len(h3)

x0 = x[0::4]
x1 = x[1::4]
x2 = x[2::4]
x3 = x[3::4]
x0_f = fft(x0)/len(x0)
x1_f = fft(x1)/len(x1)
x2_f = fft(x2)/len(x2)
x3_f = fft(x3)/len(x3)

y0_f = x0_f*h0_f/4
y1_f = x3_f*h1_f/4
y2_f = x2_f*h2_f/4
y3_f = x1_f*h3_f/4

y0 = ifft(y0_f)*1000
y1 = ifft(y1_f)*1000
y2 = ifft(y2_f)*1000
y3 = ifft(y3_f)*1000


y_filt_poly = np.roll(y0, 0) + np.roll(y1, 1)  + np.roll(y2, 1) + np.roll(y3, 1)

y_filt_poly_f = fft(y_filt_poly)/len(y_filt_poly)

In [205]:
fig_nonideal_filter_downsamp = plot_complex_spectrum(x0_f, name='x0', add_axis=True, IQ_limit=3, color='#636EFA', plot_title="Polyphase Components of Non-ideal LPF")
fig_nonideal_filter_downsamp = plot_complex_spectrum(x1_f, name='x1', add_axis=True, IQ_limit=3, color='#EF553B', plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)
fig_nonideal_filter_downsamp = plot_complex_spectrum(x2_f, name='x2', add_axis=True, IQ_limit=3, color='#00CC96', plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)
fig_nonideal_filter_downsamp = plot_complex_spectrum(x3_f, name='x3', add_axis=True, IQ_limit=3, color='#AB63FA', plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)

fig_nonideal_filter_downsamp = plot_complex_spectrum(h0_f, name='h0', add_axis=True, IQ_limit=3, color='#636EFA', scatter_mode='lines', dash='dash', line_width = 3, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)
fig_nonideal_filter_downsamp = plot_complex_spectrum(h3_f, name='h3', add_axis=True, IQ_limit=3, color='#EF553B', scatter_mode='lines', dash='dash', line_width = 3, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)
fig_nonideal_filter_downsamp = plot_complex_spectrum(h2_f, name='h2', add_axis=True, IQ_limit=3, color='#00CC96', scatter_mode='lines', dash='dash', line_width = 3, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)
fig_nonideal_filter_downsamp = plot_complex_spectrum(h1_f, name='h1', add_axis=True, IQ_limit=3, color='#AB63FA', scatter_mode='lines', dash='dash', line_width = 3, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_downsamp)

fig_nonideal_filter_downsamp.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.0, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))
# fig_nonideal_filter_downsamp.show()

fig_nonideal_filter_downsamp.write_html("nonideal_filter_downsamp.html",
                                 include_plotlyjs='cdn',
                                 full_html=False,)

In [206]:
fig_nonideal_filter_output = plot_complex_spectrum(y0_f, name='y0', add_axis=True, IQ_limit=1.5, plot_title="Output of Non-ideal Polyphase Filter Bank")
fig_nonideal_filter_output = plot_complex_spectrum(y1_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='y1', add_axis=True, IQ_limit=1.5, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_output)
fig_nonideal_filter_output = plot_complex_spectrum(y2_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='y2', add_axis=True, IQ_limit=1.5, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_output)
fig_nonideal_filter_output = plot_complex_spectrum(y3_f*np.exp(-1j*2*np.pi*np.arange(1000)/1000), name='y3', add_axis=True, IQ_limit=1.5, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_output)
fig_nonideal_filter_output = plot_complex_spectrum(y_filt_poly_f, name='y', add_axis=True, IQ_limit=1, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_output)
# fig_nonideal_filter_output = plot_complex_spectrum((filter_freq_response*x_f_0)[0:1000], name='Decimation Filter Output', add_axis=True, IQ_limit=1.5, plot_title="Polyphase Components of Non-ideal LPF", fig = fig_nonideal_filter_output)


fig_nonideal_filter_output.update_layout(width=800, height=450,
                          scene=dict(
                            aspectmode="manual",           # allow manual control
                            aspectratio=dict(x=1.0, y=0.5, z=0.5),  # scale of each axis
                            camera=dict(eye=dict(x=-0.75, y=-1.5, z=0.55),
                                        up=dict(x=0, y=0, z=1),
                                        center=dict(x=0, y=0, z=-0.2),),  # adjust the camera so labels are visible,
                        ))
fig_nonideal_filter_output.write_html("nonideal_filter_output.html",
                                 include_plotlyjs='cdn',
                                 full_html=False,)

In [84]:
fig_filter_downsamp.write_html("nonideal_filter_downsamp.html",
                                include_plotlyjs='cdn',
                                full_html=False,)

# Scratch 

In [62]:
x = np.random.randn(12)
h = np.random.randn(6)

y_filt_down = ifft(fft(x,12)*fft(h,12))
y_filt_down = y_filt_down[0::3]

h0 = h[0::3]
h1 = h[1::3]
h2 = h[2::3]

x0 = x[0::3]
x1 = x[1::3]
x2 = x[2::3]

y0 = ifft(fft(x0,4)*fft(h0,4))
y1 = ifft(fft(x2,4)*fft(h1,4))
y2 = ifft(fft(x1,4)*fft(h2,4))

y_filt_poly = np.roll(y0, 0) + np.roll(y1, 1)  + np.roll(y2, 1)